### Creating star schema ; dimensions and fact tables that I will use in queries

#### Kreiranje Delta Tabela

In [0]:
%sql
CREATE SCHEMA IF NOT EXISTS gold;

In [0]:
%sql
CREATE TABLE gold.dim_customers
USING DELTA
LOCATION 'dbfs:/FileStore/MedallionArchitecture/gold/Dim_Customers';

CREATE TABLE gold.dim_products
USING DELTA
LOCATION 'dbfs:/FileStore/MedallionArchitecture/gold/Dim_Products';

CREATE TABLE gold.dim_shippers
USING DELTA
LOCATION 'dbfs:/FileStore/MedallionArchitecture/gold/Dim_Shippers';

CREATE TABLE gold.dim_orderdate
USING DELTA
LOCATION "dbfs:/FileStore/MedallionArchitecture/gold/Dim_Order_Date";

CREATE TABLE gold.dim_shipmentdate
USING DELTA
LOCATION "dbfs:/FileStore/MedallionArchitecture/gold/Dim_Shipment_Date";


CREATE TABLE gold.factFINALtable
USING DELTA
LOCATION "dbfs:/FileStore/MedallionArchitecture/gold/FactTableFINAL"


In [0]:
%sql
SELECT COUNT(DISTINCT(OrderId))
FROM silver.orderdetails

count(DISTINCT OrderId) 6571

In [0]:
%sql
SELECT od.OrderID
FROM silver.orderdetails od
LEFT JOIN silver.orders o ON od.OrderID = o.OrderID
WHERE o.CustomerID IS NULL;


OrderID

In [0]:
%sql
SELECT COUNT(DISTINCT(OrderID))
FROM silver.orders;

count(DISTINCT OrderID) 4266

In [0]:
# Load Silver Layer Tables
df_article_categories = spark.read.format("delta").load("dbfs:/FileStore/MedallionArchitecture/silver/ArticleCategories")
df_customers = spark.read.format("delta").load("dbfs:/FileStore/MedallionArchitecture/silver/Customers")
df_divisions = spark.read.format("delta").load("dbfs:/FileStore/MedallionArchitecture/silver/Divisions")
df_order_details = spark.read.format("delta").load("dbfs:/FileStore/MedallionArchitecture/silver/OrderDetails")
df_orders = spark.read.format("delta").load("dbfs:/FileStore/MedallionArchitecture/silver/Orders")
df_products = spark.read.format("delta").load("dbfs:/FileStore/MedallionArchitecture/silver/Products")
df_shipments = spark.read.format("delta").load("dbfs:/FileStore/MedallionArchitecture/silver/Shipments")
df_shippers = spark.read.format("delta").load("dbfs:/FileStore/MedallionArchitecture/silver/Shippers")

#### kreiranje dimenzije Dim_Customers

In [0]:
%sql
SELECT *
FROM silver.Customers
LIMIT 20;

CustomerID CompanyName ContactName City Country DivisionID Address Fax Phone PostalCode StateProvince Street StreetNumber 62 Roba di Piel Jorge Alemaio São Paulo Brazil 4 Alameda dos Canàrios, 891 N/A 115551189 05487020 N/A Alameda dos Canàrios 891 35 El Zapato Rojo Nicolas Balines San Cristóbal Venezuela 4 Carrera 22 con Ave. Carlos Soublette #8-35 55551948 55551340 5022 N/A Carrera con Ave. Carlos Soublette #8-35 22 6 Man Kleider Herman Hinschler Mannheim Germany 1 Forsterstr. 57 062108924 062108460 68306 N/A Forsterstr 57 9 La Legion Mercenaire Bernard de Gaule Marseille France 1 12, rue des Bouchers 91244541 91244540 13008 N/A rue des Bouchers 12 13 Los Sombreros Gigantes Speedy Gonzales México D.F. Mexico 2 El Barrio Chino 12 55557293 55553392 5021 N/A El Barrio Chino 12 16 The sharped dressed man Ian Wright London UK 1 Berkeley Gardens
 N/A N/A N/A N/A Berkeley Gardens N/A 73 Rode & Vite Preben Elkjaer København Denmark 3 Vinbæltet 34 31133557 1234 1734 N/A Vinbæltet 34 52 Kohl Industries AG Helmuth Klein Leipzig Germany 1 Heerstr. 22 N/A 0342023176 4179 N/A Heerstr 22 14 Das Alpen Shoe Alfred Neumann Bern Switzerland 1 Hauptstr. 29 N/A 0452076545 3012 N/A Hauptstr 29 59 Extrawagens Herbert Bernstorf Salzburg Austria 1 Geislweg 14 65629723 65629722 5020 N/A Geislweg 14 67 Da Bikini Expertu Thomá Lindao Rio de Janeiro Brazil 4 Av. Copacabana, 267 N/A 215553412 02389890 N/A Av. Copacabana 267 84 Art et Fashion Pierre Robert Lyon France 1 2, rue du Commerce 78325487 78325486 69004 N/A rue du Commerce 2 50 De la Vita Marco Van Deum Bruxelles Belgium 1 Rue Joseph-Bens 532 022012468 022012467 B1180 N/A Rue Joseph-Bens 532 58 La Moda Pasada Francisca Font Barceló México D.F. Mexico 2 Calle Dr. Jorge Cash 321 55453745 55523745 5033 N/A Calle Dr. Jorge Cash 321 127 Stephanies Staffan Blond Stockholm Sweden 3 Gatauppochner. 1 8112233 8102030 11111 N/A Gatauppochner 1 91 Slotzy Danz Boniekk Wallessa Warszawa Poland 1 ul. Filtrowa 68 266427012 266427012 01012 N/A ul. Filtrowa 68 41 Elle Fashion & Design Louise Davu Toulouse France 1 1 rue Alsace-Lorraine 61776111 61776110 31000 N/A rue Alsace-Lorraine 1 57 Jazz Style Fashion& Art Dizzi Gillespi Paris France 1 265, boulevard Charonne 142342277 142342266 75012 N/A boulevard Charonne 265 21 Cloe do Pau Romario do Sauza São Paulo Brazil 4 Rua Orós, 92 N/A 115559857 05442030 N/A Rua Orós 92 71 Sunny Ski Store Perry Farell Boise USA 2 187 Suffolk Ln. N/A 2085558097 83720 ID Suffolk Ln 187

In [0]:
%sql
SELECT sc.CompanyName, sd.Division, sd.Subdivision
FROM silver.Customers AS sc
INNER JOIN silver.divisions AS sd
ON
sc.DivisionID = sd.DivisionID

CompanyName Division Subdivision Roba di Piel South America South America El Zapato Rojo South America South America Man Kleider Europe Europe La Legion Mercenaire Europe Europe Los Sombreros Gigantes North America North America The sharped dressed man Europe Europe Rode & Vite Europe Scandinavia Kohl Industries AG Europe Europe Das Alpen Shoe Europe Europe Extrawagens Europe Europe Da Bikini Expertu South America South America Art et Fashion Europe Europe De la Vita Europe Europe La Moda Pasada North America North America Stephanies Europe Scandinavia Slotzy Danz Europe Europe Elle Fashion & Design Europe Europe Jazz Style Fashion& Art Europe Europe Cloe do Pau South America South America Sunny Ski Store North America North America Belgium Black Jeans Europe Europe Boleros Europe Europe Macalena North America North America Los Pantalones Magicos South America South America Los Vatos Locos South America South America Alles Lusekofter Europe Scandinavia Warp AG Europe Europe Los Trajes de Matador Europe Europe For The Dark Night North America North America Eye Fashion North America North America Perkii Urkii Europe Scandinavia SSS-Sport Shoes Store North America North America El Abrigo Mortal South America South America Menàge à Trois Europe Europe Bond Ltd North America North America Golden Design Group Europe Europe Don Balón North America North America Dr Jims Trousers Europe Europe Big Foot Shoes North America North America Tendha do Flamengo South America South America Champes Europe Europe Il Pantaloni di la Cammorra Europe Europe Nirvana Stores North America North America Noch Einmal GMBH Europe Europe Halle Köln Europe Europe Pour l´homme Europe Europe Da Santho Cosmethia South America South America La Camisas Cansadas Europe Europe Th Fashing Europe Europe Gluderstedt Europe Europe Sport & Fritid AB Europe Scandinavia La Ropa Vieja North America North America Copacabana South America South America El Carnevale South America South America El Pirata South America South America Sport Shop Europe Europe Los Espandrilos Fantasticos South America South America Pulp Toxedos North America North America The Corner Store North America North America La Tienda de la Esquina North America North America Fast Sunglasses Europe Europe Le Sais de Rión Europe Europe Modehuset Abel Europe Scandinavia Paintho da Gama South America South America Autokleider Europe Europe Las Corbatas Europe Europe King Size Clothes Europe Europe Shoe Expert Europe Europe Too Hot 4U North America North America Urras Shop Europe Scandinavia La Moda Alucinante Europe Europe El Traige do Benfica Europe Europe Ski Store Europe Europe La Moda d'il Futuri Europe Europe Bobby Socks North America North America Davenport Fashion North America North America Eintrach GS Europe Europe Boombastic Europe Europe Casual Clothing Europe Europe Fawtly Towers Europe Europe Aujourd´hui Europe Europe Leningrad Cowboys Shop Europe Scandinavia Chateau de Ville Europe Europe Grunewald Europe Europe La Boheme Europe Europe Millenium North America North America El Chandal del Barca Europe Europe X-Site North America North America TTT-The Ticky Tie North America North America Merced do Vaile South America South America Ropa total South America South America La Roba do Santho Europe Europe

In [0]:
df_dim_customers = (
    df_customers.join(df_divisions, "DivisionID", "left").select("CustomerID", "CompanyName", "ContactName", "City", "Country", 
            "Division", "Subdivision","Address", "Street", "PostalCode", "Phone")  
)

# Save to Gold Layer
df_dim_customers.write.format("delta").mode("overwrite").save("dbfs:/FileStore/MedallionArchitecture/gold/Dim_Customers")

#### kreiranje dimenzije Dim_Products

In [0]:
%sql
SELECT *
FROM silver.Products
LIMIT 20;

ProductID ProductName SupplierID CategoryID QuantityPerUnit UnitCost UnitPrice UnitsInStock UnitsOnOrder Margin_Percent Profit 1 Lenin Jeansshorts 1 1 10 15.37 20.0 39 0 23.15 4.63 2 Mr2 Trousers 1 1 10 16.17 19.0 17 40 14.89 2.83 3 Chantell Shirt 1 2 20 15.45 20.0 13 70 22.75 4.55 4 Rossi Shorts 2 2 15 19.34 22.0 53 0 12.09 2.66 5 O-Man Underwear 2 1 100 4.72 6.0 0 0 21.33 1.28 6 Shagall Socks 3 2 50 3.21 4.0 120 0 19.75 0.79 7 Runner Shoes 3 7 40 33.11 40.0 15 0 17.23 6.89 8 Tuxedo Top 3 2 20 16.14 20.0 6 0 19.3 3.86 9 Fuji Boots 4 6 10 32.9 39.0 29 0 15.64 6.1 10 Sapporoo Gloves 4 8 20 6.2 7.0 31 0 11.43 0.8 11 Desperado Jeans 5 1 25 21.1 28.0 22 30 24.64 6.9 12 Tank Swimsuit 5 4 20 7.92 10.0 86 0 20.8 2.08 13 Aino Shoes 6 8 25 21.11 25.0 24 0 15.56 3.89 14 Kool Sunglasses 6 7 21 20.36 23.25 35 0 12.43 2.89 15 Sumi Underwear 6 2 30 4.98 6.5 39 0 23.38 1.52 16 Wimbledon T-Shirt 7 3 24 7.33 9.45 29 0 22.43 2.12 17 TieBreak Tennis shoes 7 6 36 19.35 25.0 0 0 22.6 5.65 18 Deuce Shirt 7 8 18 22.09 25.5 42 0 13.37 3.41 19 Squash Shorts 8 3 1 7.4 9.2 25 0 19.57 1.8 20 Tennis Suit 8 3 1 64.49 81.0 40 0 20.38 16.51

In [0]:
dbutils.fs.rm("dbfs:/FileStore/MedallionArchitecture/gold/Dim_Products",True)

Out[11]: True

In [0]:
df_products = spark.read.format("delta").load("dbfs:/FileStore/MedallionArchitecture/silver/Products")
df_article_categories = spark.read.format("delta").load("dbfs:/FileStore/MedallionArchitecture/silver/ArticleCategories")
df_dim_products = (
    df_products
    .join(df_article_categories, "CategoryID", "left") 
    .select("ProductID", "ProductName", "Category", "SubCategory")
)

# Save to Gold Layer
df_dim_products.write.format("delta").mode("overwrite").save("dbfs:/FileStore/MedallionArchitecture/gold/Dim_Products")


In [0]:
%sql
CREATE TABLE gold.dim_products
USING DELTA
LOCATION "dbfs:/FileStore/MedallionArchitecture/gold/Dim_Products"

In [0]:
%sql
SELECT *
FROM gold.dim_products

ProductID ProductName Category SubCategory 1 Lenin Jeansshorts Clothes Men's Clothes 2 Mr2 Trousers Clothes Men's Clothes 3 Chantell Shirt Clothes Women's Clothes 4 Rossi Shorts Clothes Women's Clothes 5 O-Man Underwear Clothes Men's Clothes 6 Shagall Socks Clothes Women's Clothes 7 Runner Shoes Clothes Children's Clothes 8 Tuxedo Top Clothes Women's Clothes 9 Fuji Boots Footwear Men's Footwear 10 Sapporoo Gloves Clothes Baby Clothes 11 Desperado Jeans Clothes Men's Clothes 12 Tank Swimsuit Swimwear Swimwear 13 Aino Shoes Clothes Baby Clothes 14 Kool Sunglasses Clothes Children's Clothes 15 Sumi Underwear Clothes Women's Clothes 16 Wimbledon T-Shirt Sportswear Sportswear 17 TieBreak Tennis shoes Footwear Men's Footwear 18 Deuce Shirt Clothes Baby Clothes 19 Squash Shorts Sportswear Sportswear 20 Tennis Suit Sportswear Sportswear 21 Basket Shoes Sportswear Sportswear 22 Ravellis Träskor Footwear Women's Footwear 23 DSW Sandals Footwear Women's Footwear 24 Samba Soccer Socks Clothes Men's Clothes 25 Basket Vest Sportswear Sportswear 26 Bike Helmet Sportswear Sportswear 27 Tracksuit Sportswear Sportswear 28 RDL Suit Clothes Children's Clothes 29 Davenport Shoes Footwear Men's Footwear 30 Baby Dark Lounge Suit Clothes Baby Clothes 31 Rossi Bermuda Shorts Clothes Men's Clothes 32 Riviera Swimsuit Swimwear Swimwear 33 Casual Boots Sportswear Sportswear 34 Baywatch Swimsuit Swimwear Swimwear 35 LA. Shorts Swimwear Swimwear 36 Mehmet-Tröja Clothes Baby Clothes 37 Mehmet-Skor Clothes Baby Clothes 38 Le Baby Dress Clothes Women's Clothes 39 Terence Top Clothes Women's Clothes 40 Duck Trousers Clothes Baby Clothes 41 Duck Shirt Clothes Baby Clothes 42 Walking Shoes Footwear Women's Footwear 43 Summer Shorts Swimwear Swimwear 44 Okkaba Skin Jackets Clothes Women's Clothes 45 Danske Treshoe Footwear Men's Footwear 46 Rodbye Troje Clothes Baby Clothes 47 Lundenhagen Boots Footwear Men's Footwear 48 Root Boot Footwear Men's Footwear 49 Finnish Sport Blades Sportswear Sportswear 50 Finnish Swimsuit Swimwear Swimwear 51 Summit Hiking Boots Footwear Men's Footwear 52 Winter Boots Footwear Women's Footwear 53 Jack Flash Dress Clothes Women's Clothes 54 Patamonia Fleece Jacket Sportswear Sportswear 55 Feiss Fleece Trousers Sportswear Sportswear 56 Slip-on Shoes Footwear Women's Footwear 57 Lightweight Sandals Footwear Women's Footwear 58 Onesy Dress Clothes Baby Clothes 59 Rasta WCT Sportswear Sportswear 60 Game Over T-Shirt Sportswear Sportswear 61 AAA Running Shoe Sportswear Sportswear 62 Lace Shoes Sportswear Sportswear 63 Serve-Shirt Clothes Women's Clothes 64 WFS Shoes Footwear Women's Footwear 65 Stretch Pants Clothes Women's Clothes 66 Langoste Shirt Clothes Women's Clothes 67 Minnki Pälsii Clothes Women's Clothes 68 Cap Sportswear Sportswear 69 Tube Socks Sportswear Sportswear 70 US-Master Jeans Clothes Men's Clothes 71 Atles Lussekofta Clothes Men's Clothes 72 Oyaki Kimono Clothes Women's Clothes 73 Mehmet-Napp Clothes Baby Clothes 74 X-Train Shoes Clothes Children's Clothes 75 Bow tie Clothes Men's Clothes 76 Halter Dress Clothes Women's Clothes 77 Wrap Skirt Clothes Women's Clothes

### dimenzija dim Shippers

In [0]:
df_dim_shippers = df_shippers.select("ShipperID", "CompanyName")
df_dim_shippers.write.format("delta").mode("overwrite").save("dbfs:/FileStore/MedallionArchitecture/gold/Dim_Shippers")

### dimenzija Date that I decided not to use (instead I incorporated logic of using dimesion order and dimension shipment date)

In [0]:
from pyspark.sql.functions import col, year, month, quarter
df_dim_date = (
    df_orders.select(col("OrderDate").alias("Date"))
    .union(df_shipments.select(col("ShipmentDate").alias("Date")))
    .distinct()
    .withColumn("Year", year(col("Date")))
    .withColumn("Month", month(col("Date")))
    .withColumn("Quarter", quarter(col("Date")))
)
df_dim_date.write.format("delta").mode("overwrite").save("dbfs:/FileStore/MedallionArchitecture/gold/Dim_Date")


In [0]:
dbutils.fs.rm("dbfs:/FileStore/MedallionArchitecture/gold/Dim_Date", recurse=True)

Out[13]: True

In [0]:
from pyspark.sql.functions import col, year, month, quarter, monotonically_increasing_id

df_dim_date = (
    df_orders.select(col("OrderDate").alias("Date"))
    .union(df_shipments.select(col("ShipmentDate").alias("Date")))
    .distinct()
    .withColumn("Year", year(col("Date")))
    .withColumn("Month", month(col("Date")))
    .withColumn("Quarter", quarter(col("Date")))
    .withColumn("DateKey", monotonically_increasing_id())  # Generate unique DateKey
)

# Save the updated Date Dimension table
df_dim_date.write.format("delta").mode("overwrite").save("dbfs:/FileStore/MedallionArchitecture/gold/Dim_Date")

In [0]:
%sql
CREATE TABLE gold.dim_date
USING DELTA
LOCATION 'dbfs:/FileStore/MedallionArchitecture/gold/Dim_Date';

In [0]:
%sql
SELECT *
FROM gold.dim_date

Date Year Month Quarter DateKey 2007-11-23 2007 11 4 0 2010-08-11 2010 8 3 1 2009-07-25 2009 7 3 2 2009-11-22 2009 11 4 3 2011-01-29 2011 1 1 4 2011-01-30 2011 1 1 5 2011-10-07 2011 10 4 6 2009-09-27 2009 9 3 7 2010-09-24 2010 9 3 8 2009-06-28 2009 6 2 9 2009-08-09 2009 8 3 10 2011-05-06 2011 5 2 11 2009-10-19 2009 10 4 12 2007-04-19 2007 4 2 13 2008-07-15 2008 7 3 14 2009-05-13 2009 5 2 15 2009-06-25 2009 6 2 16 2010-08-16 2010 8 3 17 2009-02-14 2009 2 1 18 2008-02-01 2008 2 1 19 2011-07-07 2011 7 3 20 2010-04-15 2010 4 2 21 2011-01-23 2011 1 1 22 2011-07-18 2011 7 3 23 2011-08-21 2011 8 3 24 2011-11-18 2011 11 4 25 2010-12-15 2010 12 4 26 2010-07-19 2010 7 3 27 2012-02-12 2012 2 1 28 2009-03-12 2009 3 1 29 2008-01-20 2008 1 1 30 2010-06-10 2010 6 2 31 2010-12-01 2010 12 4 32 2010-02-20 2010 2 1 33 2010-05-23 2010 5 2 34 2010-06-19 2010 6 2 35 2012-03-30 2012 3 1 36 2010-04-14 2010 4 2 37 2011-11-14 2011 11 4 38 2008-09-02 2008 9 3 39 2009-08-02 2009 8 3 40 2011-09-04 2011 9 3 41 2010-08-25 2010 8 3 42 2010-09-22 2010 9 3 43 2009-05-01 2009 5 2 44 2008-06-24 2008 6 2 45 2008-04-28 2008 4 2 46 2011-04-06 2011 4 2 47 2011-08-30 2011 8 3 48 2010-07-22 2010 7 3 49 2008-05-31 2008 5 2 50 2009-08-21 2009 8 3 51 2009-11-08 2009 11 4 52 2011-07-02 2011 7 3 53 2010-06-11 2010 6 2 54 2009-10-15 2009 10 4 55 2010-05-31 2010 5 2 56 2011-07-06 2011 7 3 57 2011-07-09 2011 7 3 58 2011-04-27 2011 4 2 59 2009-07-12 2009 7 3 60 2011-10-23 2011 10 4 61 2008-06-28 2008 6 2 62 2011-08-05 2011 8 3 63 2008-03-29 2008 3 1 64 2010-02-18 2010 2 1 65 2008-07-25 2008 7 3 66 2010-07-11 2010 7 3 67 2009-12-11 2009 12 4 68 2008-07-04 2008 7 3 69 2011-04-29 2011 4 2 70 2008-04-25 2008 4 2 71 2009-03-29 2009 3 1 72 2011-08-16 2011 8 3 73 2009-04-02 2009 4 2 74 2010-11-22 2010 11 4 75 2010-04-16 2010 4 2 76 2009-06-15 2009 6 2 77 2011-05-22 2011 5 2 78 2011-01-25 2011 1 1 79 2010-04-04 2010 4 2 80 2011-06-05 2011 6 2 81 2009-09-14 2009 9 3 82 2008-03-22 2008 3 1 83 2009-10-08 2009 10 4 84 2009-11-06 2009 11 4 85 2011-10-06 2011 10 4 86 2008-01-26 2008 1 1 87 2009-11-10 2009 11 4 88 2009-06-07 2009 6 2 89 2009-11-07 2009 11 4 90 2011-03-27 2011 3 1 91 2011-05-02 2011 5 2 92 2010-05-04 2010 5 2 93 2010-07-24 2010 7 3 94 2010-06-16 2010 6 2 95 2008-10-08 2008 10 4 96 2010-03-19 2010 3 1 97 2009-05-03 2009 5 2 98 2010-02-02 2010 2 1 99 2011-09-17 2011 9 3 100 2011-05-11 2011 5 2 101 2010-02-07 2010 2 1 102 2008-10-25 2008 10 4 103 2009-02-27 2009 2 1 104 2011-09-02 2011 9 3 105 2009-06-24 2009 6 2 106 2009-09-09 2009 9 3 107 2012-03-05 2012 3 1 108 2011-03-29 2011 3 1 109 2011-10-15 2011 10 4 110 2011-10-13 2011 10 4 111 2011-02-19 2011 2 1 112 2009-07-30 2009 7 3 113 2011-09-25 2011 9 3 114 2011-06-13 2011 6 2 115 2011-12-24 2011 12 4 116 2011-04-09 2011 4 2 117 2011-04-07 2011 4 2 118 2008-07-02 2008 7 3 119 2012-01-31 2012 1 1 120 2009-03-15 2009 3 1 121 2008-11-09 2008 11 4 122 2007-11-30 2007 11 4 123 2012-03-27 2012 3 1 124 2008-03-08 2008 3 1 125 2011-10-16 2011 10 4 126 2011-06-07 2011 6 2 127 2010-02-04 2010 2 1 128 2008-09-18 2008 9 3 129 2010-04-21 2010 4 2 130 2010-06-23 2010 6 2 131 2009-01-30 2009 1 1 132 2010-12-18 2010 12 4 133 2009-01-22 2009 1 1 134 2007-11-21 2007 11 4 135 2011-08-17 2011 8 3 136 2008-04-23 2008 4 2 137 2011-03-18 2011 3 1 138 2010-10-06 2010 10 4 139 2012-01-06 2012 1 1 140 2009-03-30 2009 3 1 141 2008-08-05 2008 8 3 142 2009-05-27 2009 5 2 143 2011-03-07 2011 3 1 144 2009-04-03 2009 4 2 145 2009-05-11 2009 5 2 146 2010-07-18 2010 7 3 147 2011-04-19 2011 4 2 148 2009-07-14 2009 7 3 149 2011-05-14 2011 5 2 150 2011-09-07 2011 9 3 151 2011-10-20 2011 10 4 152 2010-09-19 2010 9 3 153 2010-07-23 2010 7 3 154 2008-09-06 2008 9 3 155 2009-11-17 2009 11 4 156 2008-08-14 2008 8 3 157 2008-08-11 2008 8 3 158 2011-08-02 2011 8 3 159 2011-05-17 2011 5 2 160 2009-08-06 2009 8 3 161 2010-08-09 2010 8 3 162 2009-10-06 2009 10 4 163 2009-12-09 2009 12 4 164 2008-06-06 2008 6 2 165 2010-11-04 2010 11 4 166 2009-11-27 2009 11 4 167 2010-08-10 

In [0]:
%sql
DROP TABLE IF EXISTS gold.dim_date

### Fact tabela Sales

In [0]:
%sql
SELECT *
FROM silver.products

ProductID ProductName SupplierID CategoryID QuantityPerUnit UnitCost UnitPrice UnitsInStock UnitsOnOrder Margin_Percent Profit 1 Lenin Jeansshorts 1 1 10 15.37 20.0 39 0 23.15 4.63 2 Mr2 Trousers 1 1 10 16.17 19.0 17 40 14.89 2.83 3 Chantell Shirt 1 2 20 15.45 20.0 13 70 22.75 4.55 4 Rossi Shorts 2 2 15 19.34 22.0 53 0 12.09 2.66 5 O-Man Underwear 2 1 100 4.72 6.0 0 0 21.33 1.28 6 Shagall Socks 3 2 50 3.21 4.0 120 0 19.75 0.79 7 Runner Shoes 3 7 40 33.11 40.0 15 0 17.23 6.89 8 Tuxedo Top 3 2 20 16.14 20.0 6 0 19.3 3.86 9 Fuji Boots 4 6 10 32.9 39.0 29 0 15.64 6.1 10 Sapporoo Gloves 4 8 20 6.2 7.0 31 0 11.43 0.8 11 Desperado Jeans 5 1 25 21.1 28.0 22 30 24.64 6.9 12 Tank Swimsuit 5 4 20 7.92 10.0 86 0 20.8 2.08 13 Aino Shoes 6 8 25 21.11 25.0 24 0 15.56 3.89 14 Kool Sunglasses 6 7 21 20.36 23.25 35 0 12.43 2.89 15 Sumi Underwear 6 2 30 4.98 6.5 39 0 23.38 1.52 16 Wimbledon T-Shirt 7 3 24 7.33 9.45 29 0 22.43 2.12 17 TieBreak Tennis shoes 7 6 36 19.35 25.0 0 0 22.6 5.65 18 Deuce Shirt 7 8 18 22.09 25.5 42 0 13.37 3.41 19 Squash Shorts 8 3 1 7.4 9.2 25 0 19.57 1.8 20 Tennis Suit 8 3 1 64.49 81.0 40 0 20.38 16.51 21 Basket Shoes 8 3 1 8.78 10.0 3 40 12.2 1.22 22 Ravellis Träskor 9 5 90 2.65 3.5 104 0 24.29 0.85 23 DSW Sandals 9 5 100 7.43 9.0 61 0 17.44 1.57 24 Samba Soccer Socks 10 1 100 3.9 4.5 20 0 13.33 0.6 25 Basket Vest 11 3 1 10.85 14.0 76 0 22.5 3.15 26 Bike Helmet 11 3 1 26.13 31.23 15 0 16.33 5.1 27 Tracksuit 11 3 1 36.06 43.9 49 0 17.86 7.84 28 RDL Suit 12 7 1 36.81 45.6 26 0 19.28 8.79 29 Davenport Shoes 12 6 1 100.74 123.79 0 0 18.62 23.05 30 Baby Dark Lounge Suit 13 8 1 22.71 25.89 10 0 12.28 3.18 31 Rossi Bermuda Shorts 14 1 20 7.53 8.5 0 70 11.41 0.97 32 Riviera Swimsuit 14 4 30 15.12 19.0 9 40 20.42 3.88 33 Casual Boots 15 3 25 20.2 25.5 112 0 20.78 5.3 34 Baywatch Swimsuit 16 4 12 6.76 8.0 111 0 15.5 1.24 35 LA. Shorts 16 4 14 5.17 6.0 20 0 13.83 0.83 36 Mehmet-Tröja 17 8 20 6.45 8.0 112 0 19.37 1.55 37 Mehmet-Skor 17 8 21 3.43 4.0 11 50 14.25 0.57 38 Le Baby Dress 18 2 4 62.38 80.5 17 0 22.51 18.12 39 Terence Top 18 2 3 48.17 60.0 69 0 19.72 11.83 40 Duck Trousers 19 8 1 16.34 18.4 123 0 11.2 2.06 41 Duck Shirt 19 8 1 7.28 9.65 85 0 24.56 2.37 42 Walking Shoes 20 5 1 10.95 14.0 26 0 21.79 3.05 43 Summer Shorts 20 4 1 10.48 12.0 17 10 12.67 1.52 44 Okkaba Skin Jackets 20 2 7 67.17 75.45 27 0 10.97 8.28 45 Danske Treshoe 21 6 100 8.44 9.5 5 70 11.16 1.06 46 Rodbye Troje 21 8 40 9.07 12.0 95 0 24.42 2.93 47 Lundenhagen Boots 22 6 14 22.12 25.5 36 0 13.25 3.38 48 Root Boot 22 6 25 28.35 32.75 15 70 13.44 4.4 49 Finnish Sport Blades 23 3 1 15.43 20.0 10 60 22.85 4.57 50 Finnish Swimsuit 23 4 1 13.57 16.25 65 0 16.49 2.68 51 Summit Hiking Boots 24 6 10 82.74 99.9 20 0 17.18 17.16 52 Winter Boots 24 5 14 70.81 80.0 38 0 11.49 9.19 53 Jack Flash Dress 24 2 6 52.38 60.8 0 0 13.85 8.42 54 Patamonia Fleece Jacket 25 3 24 30.27 35.45 21 0 14.61 5.18 55 Feiss Fleece Trousers 25 3 20 33.18 39.0 115 0 14.92 5.82 56 Slip-on Shoes 26 5 15 34.17 38.0 21 10 10.08 3.83 57 Lightweight Sandals 26 5 20 16.14 19.5 36 0 17.23 3.36 58 Onesy Dress 27 8 20 37.17 48.25 62 0 22.96 11.08 59 Rasta WCT 28 3 105 6.69 8.5 79 0 21.29 1.81 60 Game Over T-Shirt 28 3 53 4.44 5.0 19 0 11.2 0.56 61 AAA Running Shoe 29 3 20 22.24 26.5 113 0 16.08 4.26 62 Lace Shoes 29 3 30 25.39 29.3 17 0 13.34 3.91 63 Serve-Shirt 7 2 68 15.9 19.9 24 0 20.1 4.0 64 WFS Shoes 12 5 1 29.25 33.25 22 80 12.03 4.0 65 Stretch Pants 2 2 40 8.68 10.05 76 0 13.63 1.37 66 Langoste Shirt 2 2 15 16.58 19.0 4 100 12.74 2.42 67 Minnki Pälsii 16 2 26 46.1 60.0 52 0 23.17 13.9 68 Cap 8 3 1 9.67 12.5 6 10 22.64 2.83 69 Tube Socks 15 3 100 1.65 2.0 26 0 17.5 0.35 70 US-Master Jeans 7 1 15 24.98 29.0 15 10 13.86 4.02 71 Atles Lussekofta 15 1 10 26.49 30.5 26 0 13.15 4.01 72 Oyaki Kimono 14 2 30 8.96 11.8 14 0 24.07 2.84 73 Mehmet-Napp 17 8 100 0.89 1.1 101 0 19.09 0.21 74 X-Train Shoes 4 7 30 24.39 30.0 4 20 18.7 5.61 75 Bow tie 12 1 1 6.61 7.75 125 0 14.71 1.14 76 Halter Dress 23 2 2 304.

In [0]:
%sql
SELECT o.OrderID, s.ShipperID, s.ShipmentDate
FROM silver.orders o
LEFT JOIN silver.shipments s ON o.OrderID = s.OrderID
WHERE s.ShipperID IS NULL;

OrderID ShipperID ShipmentDate

### Kreiram fact tabelu. Ovde kreiram Shipment i Order date key. NE KORISTIM OVU FACT TABELU

In [0]:
# Load Other Tables
df_order_details = spark.read.table("silver.orderdetails").alias("od")
df_products = spark.read.table("silver.products").alias("p")
df_customers = spark.read.table("silver.customers").alias("c")
df_shippers = spark.read.table("silver.shippers").alias("sh")
df_dim_date = spark.read.table("gold.Dim_Date")
df_orders = spark.read.table("silver.orders").alias("o")
df_shipments = spark.read.table("silver.shipments").alias("s")

df_orders = (
    df_orders
    .join(df_dim_date.alias("d"), col("o.OrderDate") == col("d.Date"), "left")
    .select("o.*", col("d.DateKey").alias("OrderDateKey"))
    .drop("OrderDate")
)

# Join Shipments with Date Dimension to get ShipmentDateKey
df_shipments = (
    df_shipments
    .join(df_dim_date.alias("d"), col("s.ShipmentDate") == col("d.Date"), "left")
    .select("s.*", col("d.DateKey").alias("ShipmentDateKey"))
    .drop("ShipmentDate")
)

# Join Tables to Create Fact Sales with DateKeys
df_fact_sales = (
    df_order_details
    .join(df_orders, "OrderID", "inner")
    .join(df_products, "ProductID", "inner")
    .join(df_customers, "CustomerID", "left")
    .join(df_shippers, "ShipperID", "left")
    .join(df_shipments, "OrderID", "left")
)

# Select Required Columns (Now with DateKeys)
df_fact_sales = df_fact_sales.select(
   df_order_details["OrderID"],
    df_order_details["ProductID"],
    df_orders["CustomerID"], 
    df_orders["ShipperID"], 
    df_orders["OrderDateKey"], 
    df_shipments["ShipmentDateKey"], 
    df_order_details["Quantity"], 
    df_order_details["UnitPrice"],  
    df_order_details["TotalPrice"], 
    df_order_details["Total_Discount"],
    df_products["Profit"],         
    df_products["Margin_Percent"]
)

# Save FactSales Table
df_fact_sales.write.format("delta").mode("overwrite").save("dbfs:/FileStore/MedallionArchitecture/gold/FactTableSales")


In [0]:
df = spark.read.format("delta").load("dbfs:/FileStore/MedallionArchitecture/gold/FactTableSales")
display(df)

OrderID ProductID CustomerID ShipperID OrderDateKey ShipmentDateKey Quantity UnitPrice TotalPrice Total_Discount Profit Margin_Percent 15447 12 46 2 39 1430 29 12.72 313.55 55.33 2.08 20.8 15447 12 46 2 39 1430 29 12.72 313.55 55.33 2.08 20.8 15447 23 46 2 39 1430 67 11.74 668.59 117.99 1.57 17.44 15447 23 46 2 39 1430 67 11.74 668.59 117.99 1.57 17.44 10623 19 25 2 656 822 15 9.35 126.23 14.03 1.8 19.57 10623 19 25 2 656 822 15 9.35 126.23 14.03 1.8 19.57 10623 19 25 2 656 822 15 9.35 126.23 14.03 1.8 19.57 10623 19 25 2 656 822 15 9.35 126.23 14.03 1.8 19.57 10623 19 25 2 656 822 15 9.35 126.23 14.03 1.8 19.57 10623 14 25 2 656 822 21 24.21 508.41 0.0 2.89 12.43 10623 14 25 2 656 822 21 24.21 508.41 0.0 2.89 12.43 10623 14 25 2 656 822 21 24.21 508.41 0.0 2.89 12.43 10623 14 25 2 656 822 21 24.21 508.41 0.0 2.89 12.43 10623 14 25 2 656 822 21 24.21 508.41 0.0 2.89 12.43 10623 24 25 2 656 822 3 4.37 13.11 0.0 0.6 13.33 10623 24 25 2 656 822 3 4.37 13.11 0.0 0.6 13.33 10623 24 25 2 656 822 3 4.37 13.11 0.0 0.6 13.33 10623 24 25 2 656 822 3 4.37 13.11 0.0 0.6 13.33 10623 24 25 2 656 822 3 4.37 13.11 0.0 0.6 13.33 10623 35 25 2 656 822 30 6.13 165.51 18.39 0.83 13.83 10623 35 25 2 656 822 30 6.13 165.51 18.39 0.83 13.83 10623 35 25 2 656 822 30 6.13 165.51 18.39 0.83 13.83 10623 35 25 2 656 822 30 6.13 165.51 18.39 0.83 13.83 10623 35 25 2 656 822 30 6.13 165.51 18.39 0.83 13.83 10623 21 25 2 656 822 25 10.05 226.13 25.13 1.22 12.2 10623 21 25 2 656 822 25 10.05 226.13 25.13 1.22 12.2 10623 21 25 2 656 822 25 10.05 226.13 25.13 1.22 12.2 10623 21 25 2 656 822 25 10.05 226.13 25.13 1.22 12.2 10623 21 25 2 656 822 25 10.05 226.13 25.13 1.22 12.2 10817 62 39 2 566 314 25 27.05 574.81 101.44 3.91 13.34 10817 62 39 2 566 314 25 27.05 574.81 101.44 3.91 13.34 10817 62 39 2 566 314 25 27.05 574.81 101.44 3.91 13.34 10817 62 39 2 566 314 25 27.05 574.81 101.44 3.91 13.34 10817 40 39 2 566 314 60 18.08 922.08 162.72 2.06 11.2 10817 40 39 2 566 314 60 18.08 922.08 162.72 2.06 11.2 10817 40 39 2 566 314 60 18.08 922.08 162.72 2.06 11.2 10817 40 39 2 566 314 60 18.08 922.08 162.72 2.06 11.2 10817 38 39 2 566 314 30 81.73 2451.9 0.0 18.12 22.51 10817 38 39 2 566 314 30 81.73 2451.9 0.0 18.12 22.51 10817 38 39 2 566 314 30 81.73 2451.9 0.0 18.12 22.51 10817 38 39 2 566 314 30 81.73 2451.9 0.0 18.12 22.51 10817 26 39 2 566 314 40 29.96 1018.64 179.76 5.1 16.33 10817 26 39 2 566 314 40 29.96 1018.64 179.76 5.1 16.33 10817 26 39 2 566 314 40 29.96 1018.64 179.76 5.1 16.33 10817 26 39 2 566 314 40 29.96 1018.64 179.76 5.1 16.33 11141 68 73 3 442 690 41 11.21 344.71 114.9 2.83 22.64 11141 68 73 3 442 690 41 11.21 344.71 114.9 2.83 22.64 11141 68 73 3 442 690 41 11.21 344.71 114.9 2.83 22.64 11141 68 73 3 442 690 41 11.21 344.71 114.9 2.83 22.64 11141 77 73 3 442 690 40 11.87 474.8 0.0 2.05 15.77 11141 77 73 3 442 690 40 11.87 474.8 0.0 2.05 15.77 11141 77 73 3 442 690 40 11.87 474.8 0.0 2.05 15.77 11141 77 73 3 442 690 40 11.87 474.8 0.0 2.05 15.77 11141 38 73 3 442 690 57 70.7 4029.9 0.0 18.12 22.51 11141 38 73 3 442 690 57 70.7 4029.9 0.0 18.12 22.51 11141 38 73 3 442 690 57 70.7 4029.9 0.0 18.12 22.51 11141 38 73 3 442 690 57 70.7 4029.9 0.0 18.12 22.51 11141 46 73 3 442 690 2 11.26 16.89 5.63 2.93 24.42 11141 46 73 3 442 690 2 11.26 16.89 5.63 2.93 24.42 11141 46 73 3 442 690 2 11.26 16.89 5.63 2.93 24.42 11141 46 73 3 442 690 2 11.26 16.89 5.63 2.93 24.42 13623 13 17 1 1241 1568 21 24.56 515.76 0.0 3.89 15.56 13832 2 17 1 824 905 35 24.69 864.15 0.0 2.83 14.89 13832 2 17 1 824 905 35 24.69 864.15 0.0 2.83 14.89 13832 41 17 1 824 905 25 11.47 243.74 43.01 2.37 24.56 13832 41 17 1 824 905 25 11.47 243.74 43.01 2.37 24.56 11033 53 82 3 1235 1069 70 55.35 3487.05 387.45 8.42 13.85 11033 53 82 3 1235 1069 70 55.35 3487.05 387.45 8.42 13.85 11033 69 82 3 1235 1069 36 2.15 69.66 7.74 0.35 17.5 11033 69 82 3 1235 1069 36 2.15 69.66 7.74 0.35 17.5 13840 31 65 2 990 1054 45 8.02 360.9 0.0 0.97 11.41 13840 31 65 2 990 1054 45 8.02 360.9 0.0 0.97 11.41 1

In [0]:
%sql
CREATE TABLE gold.fact_table_sales
USING DELTA
LOCATION "dbfs:/FileStore/MedallionArchitecture/gold/FactTableSales"

In [0]:
%sql
SELECT *
FROM gold.fact_table_sales

OrderID ProductID CustomerID ShipperID OrderDateKey ShipmentDateKey Quantity UnitPrice TotalPrice Total_Discount Profit Margin_Percent 15447 12 46 2 39 1430 29 12.72 313.55 55.33 2.08 20.8 15447 12 46 2 39 1430 29 12.72 313.55 55.33 2.08 20.8 15447 23 46 2 39 1430 67 11.74 668.59 117.99 1.57 17.44 15447 23 46 2 39 1430 67 11.74 668.59 117.99 1.57 17.44 10623 19 25 2 656 822 15 9.35 126.23 14.03 1.8 19.57 10623 19 25 2 656 822 15 9.35 126.23 14.03 1.8 19.57 10623 19 25 2 656 822 15 9.35 126.23 14.03 1.8 19.57 10623 19 25 2 656 822 15 9.35 126.23 14.03 1.8 19.57 10623 19 25 2 656 822 15 9.35 126.23 14.03 1.8 19.57 10623 14 25 2 656 822 21 24.21 508.41 0.0 2.89 12.43 10623 14 25 2 656 822 21 24.21 508.41 0.0 2.89 12.43 10623 14 25 2 656 822 21 24.21 508.41 0.0 2.89 12.43 10623 14 25 2 656 822 21 24.21 508.41 0.0 2.89 12.43 10623 14 25 2 656 822 21 24.21 508.41 0.0 2.89 12.43 10623 24 25 2 656 822 3 4.37 13.11 0.0 0.6 13.33 10623 24 25 2 656 822 3 4.37 13.11 0.0 0.6 13.33 10623 24 25 2 656 822 3 4.37 13.11 0.0 0.6 13.33 10623 24 25 2 656 822 3 4.37 13.11 0.0 0.6 13.33 10623 24 25 2 656 822 3 4.37 13.11 0.0 0.6 13.33 10623 35 25 2 656 822 30 6.13 165.51 18.39 0.83 13.83 10623 35 25 2 656 822 30 6.13 165.51 18.39 0.83 13.83 10623 35 25 2 656 822 30 6.13 165.51 18.39 0.83 13.83 10623 35 25 2 656 822 30 6.13 165.51 18.39 0.83 13.83 10623 35 25 2 656 822 30 6.13 165.51 18.39 0.83 13.83 10623 21 25 2 656 822 25 10.05 226.13 25.13 1.22 12.2 10623 21 25 2 656 822 25 10.05 226.13 25.13 1.22 12.2 10623 21 25 2 656 822 25 10.05 226.13 25.13 1.22 12.2 10623 21 25 2 656 822 25 10.05 226.13 25.13 1.22 12.2 10623 21 25 2 656 822 25 10.05 226.13 25.13 1.22 12.2 10817 62 39 2 566 314 25 27.05 574.81 101.44 3.91 13.34 10817 62 39 2 566 314 25 27.05 574.81 101.44 3.91 13.34 10817 62 39 2 566 314 25 27.05 574.81 101.44 3.91 13.34 10817 62 39 2 566 314 25 27.05 574.81 101.44 3.91 13.34 10817 40 39 2 566 314 60 18.08 922.08 162.72 2.06 11.2 10817 40 39 2 566 314 60 18.08 922.08 162.72 2.06 11.2 10817 40 39 2 566 314 60 18.08 922.08 162.72 2.06 11.2 10817 40 39 2 566 314 60 18.08 922.08 162.72 2.06 11.2 10817 38 39 2 566 314 30 81.73 2451.9 0.0 18.12 22.51 10817 38 39 2 566 314 30 81.73 2451.9 0.0 18.12 22.51 10817 38 39 2 566 314 30 81.73 2451.9 0.0 18.12 22.51 10817 38 39 2 566 314 30 81.73 2451.9 0.0 18.12 22.51 10817 26 39 2 566 314 40 29.96 1018.64 179.76 5.1 16.33 10817 26 39 2 566 314 40 29.96 1018.64 179.76 5.1 16.33 10817 26 39 2 566 314 40 29.96 1018.64 179.76 5.1 16.33 10817 26 39 2 566 314 40 29.96 1018.64 179.76 5.1 16.33 11141 68 73 3 442 690 41 11.21 344.71 114.9 2.83 22.64 11141 68 73 3 442 690 41 11.21 344.71 114.9 2.83 22.64 11141 68 73 3 442 690 41 11.21 344.71 114.9 2.83 22.64 11141 68 73 3 442 690 41 11.21 344.71 114.9 2.83 22.64 11141 77 73 3 442 690 40 11.87 474.8 0.0 2.05 15.77 11141 77 73 3 442 690 40 11.87 474.8 0.0 2.05 15.77 11141 77 73 3 442 690 40 11.87 474.8 0.0 2.05 15.77 11141 77 73 3 442 690 40 11.87 474.8 0.0 2.05 15.77 11141 38 73 3 442 690 57 70.7 4029.9 0.0 18.12 22.51 11141 38 73 3 442 690 57 70.7 4029.9 0.0 18.12 22.51 11141 38 73 3 442 690 57 70.7 4029.9 0.0 18.12 22.51 11141 38 73 3 442 690 57 70.7 4029.9 0.0 18.12 22.51 11141 46 73 3 442 690 2 11.26 16.89 5.63 2.93 24.42 11141 46 73 3 442 690 2 11.26 16.89 5.63 2.93 24.42 11141 46 73 3 442 690 2 11.26 16.89 5.63 2.93 24.42 11141 46 73 3 442 690 2 11.26 16.89 5.63 2.93 24.42 13623 13 17 1 1241 1568 21 24.56 515.76 0.0 3.89 15.56 13832 2 17 1 824 905 35 24.69 864.15 0.0 2.83 14.89 13832 2 17 1 824 905 35 24.69 864.15 0.0 2.83 14.89 13832 41 17 1 824 905 25 11.47 243.74 43.01 2.37 24.56 13832 41 17 1 824 905 25 11.47 243.74 43.01 2.37 24.56 11033 53 82 3 1235 1069 70 55.35 3487.05 387.45 8.42 13.85 11033 53 82 3 1235 1069 70 55.35 3487.05 387.45 8.42 13.85 11033 69 82 3 1235 1069 36 2.15 69.66 7.74 0.35 17.5 11033 69 82 3 1235 1069 36 2.15 69.66 7.74 0.35 17.5 13840 31 65 2 990 1054 45 8.02 360.9 0.0 0.97 11.41 13840 31 65 2 990 1054 45 8.02 360.9 0.0 0.97 11.41 1

### Kreiranje Dim_OrderDate i Dim_ShipmentDate

In [0]:
from pyspark.sql.window import Window
from pyspark.sql.functions import col, year, month, quarter, row_number

df_orders = spark.read.table("silver.orders")
df_dim_order_date = (
    df_orders.select(col("OrderDate").alias("Date"))
    .distinct()
    .withColumn("Year", year(col("Date")))
    .withColumn("Month", month(col("Date")))
    .withColumn("Quarter", quarter(col("Date")))
)

df_dim_order_date = df_dim_order_date.withColumn(
    "DateKey", row_number().over(Window.orderBy("Date"))
)

df_dim_order_date.write.format("delta").mode("overwrite").save("dbfs:/FileStore/MedallionArchitecture/gold/Dim_Order_Date")

In [0]:
from pyspark.sql.window import Window
from pyspark.sql.functions import col, year, month, quarter, row_number

df_shipments = spark.read.table("silver.shipments")

df_dim_shipment_date = (
    df_shipments.select(col("ShipmentDate").alias("Date"))
    .distinct()
    .withColumn("Year", year(col("Date")))
    .withColumn("Month", month(col("Date")))
    .withColumn("Quarter", quarter(col("Date")))
)

# Generate Stable DateKey
df_dim_shipment_date = df_dim_shipment_date.withColumn(
    "DateKey", row_number().over(Window.orderBy("Date"))
)

df_dim_shipment_date.write.format("delta").mode("overwrite").save("dbfs:/FileStore/MedallionArchitecture/gold/Dim_Shipment_Date")


In [0]:
%sql
CREATE TABLE gold.dim_orderdate
USING DELTA
LOCATION "dbfs:/FileStore/MedallionArchitecture/gold/Dim_Order_Date";

In [0]:
%sql
CREATE TABLE gold.dim_shipmentdate
USING DELTA
LOCATION "dbfs:/FileStore/MedallionArchitecture/gold/Dim_Shipment_Date";

In [0]:
# Load Other Tables
df_order_details = spark.read.table("silver.orderdetails").alias("od")
df_products = spark.read.table("silver.products").alias("p")
df_customers = spark.read.table("silver.customers").alias("c")
df_shippers = spark.read.table("silver.shippers").alias("sh")
df_orders = spark.read.table("silver.orders").alias("o")
df_shipments = spark.read.table("silver.shipments").alias("s")

df_dim_order_date = spark.read.table("gold.Dim_OrderDate").alias("d1")
df_dim_shipment_date = spark.read.table("gold.Dim_ShipmentDate").alias("d2")

df_orders = (
    df_orders
    .join(df_dim_order_date, df_orders["OrderDate"] == df_dim_order_date["Date"], "left")
    .select("o.*", col("d1.DateKey").alias("OrderDateKey"))
    .drop("OrderDate")
)

df_shipments = (
    df_shipments
    .join(df_dim_shipment_date, df_shipments["ShipmentDate"] == df_dim_shipment_date["Date"], "left")
    .select("s.*", col("d2.DateKey").alias("ShipmentDateKey"))
    .drop("ShipmentDate")
)

df_fact_sales = (
    df_order_details
    .join(df_orders, "OrderID", "inner")
    .join(df_products, "ProductID", "inner")
    .join(df_customers, "CustomerID", "left")
    .join(df_shippers, "ShipperID", "left")
    .join(df_shipments, "OrderID", "left")
)

df_fact_sales = df_fact_sales.select(
    df_order_details["OrderID"],
    df_order_details["ProductID"],
    df_orders["CustomerID"], 
    df_orders["ShipperID"], 
    df_orders["OrderDateKey"], 
    df_shipments["ShipmentDateKey"], 
    df_order_details["Quantity"], 
    df_order_details["UnitPrice"],  
    df_order_details["TotalPrice"], 
    df_order_details["Total_Discount"],
    df_products["Profit"],         
    df_products["Margin_Percent"]
)

df_fact_sales.write.format("delta").mode("overwrite").save("dbfs:/FileStore/MedallionArchitecture/gold/FactTableFINAL")


In [0]:
%sql
CREATE TABLE gold.factFINALtable
USING DELTA
LOCATION "dbfs:/FileStore/MedallionArchitecture/gold/FactTableFINAL"

In [0]:
%sql
DROP TABLE IF EXISTS gold.fact_table_sales

In [0]:
%sql
DROP TABLE IF EXISTS gold.dim_date